In [1]:
import pandas as pd
import seaborn as sb
import matplotlib.pyplot as plt
import numpy as np
%matplotlib inline
from sklearn import preprocessing
from itertools import islice
import seaborn as sns
from sklearn.cluster import KMeans

In [2]:
dataFrame = pd.read_excel("../week2.xlsx")

#rename columns
dataFrame=dataFrame.rename(columns = {'Total DL (Bytes)' : 'totalDL','Total UL (Bytes)' : 'totalUL','Dur. (ms)' : 
                                      'dur','MSISDN/Number':'msisdn','Last Location Name':'location',
                                      'Handset Manufacturer':'manufacturer','Handset Type':'handset'
                                     })

### The following 5 cells are concerned with clustering users based on the engagement metrics.

In [3]:
sessionsCountData=dataFrame['msisdn'].value_counts()
sessionsCount=sessionsCountData.values.tolist()
msisdn=sessionsCountData.index.values
sessionPerUserDictionary = dict(zip(msisdn, sessionsCount))

durationSumDF=dataFrame.groupby('msisdn')['dur'].sum()
duration = durationSumDF.values.tolist()
msisdn=durationSumDF.index.values
durationPerUser = dict(zip(msisdn, duration))

sum_column = dataFrame["totalUL"] + dataFrame["totalDL"]
dataFrame["totalData"] = sum_column
totalDataDF=dataFrame.groupby('msisdn')['totalData'].sum()
totalData = totalDataDF.values.tolist()
msisdn=totalDataDF.index.values

totalDataUserDictionary = dict(zip(msisdn, totalData))

In [4]:
userEngagementDF=pd.DataFrame(columns=['MSISDN' ,'Session Frequency','Session Duration','Total Data'])
userEngagementDF['MSISDN']=durationPerUser.keys()

userEngagementDF['Session Frequency']=userEngagementDF['MSISDN'].map(sessionPerUserDictionary)
userEngagementDF['Session Duration']=userEngagementDF['MSISDN'].map(durationPerUser)
userEngagementDF['Total Data']= userEngagementDF['MSISDN'].map(totalDataUserDictionary)


In [5]:
x = userEngagementDF[['Session Frequency','Session Duration','Total Data']].values.astype(float)
min_max_scaler = preprocessing.MinMaxScaler()
x_scaled = min_max_scaler.fit_transform(x)
normalized = pd.DataFrame(x_scaled,columns=['Session Frequency','Session Duration','Total Data'])

In [6]:
KMean_clust= KMeans(n_clusters=3, init='k-means++',max_iter=1000)
KMean_clust.fit(normalized)

KMeans(algorithm='auto', copy_x=True, init='k-means++', max_iter=1000,
       n_clusters=3, n_init=10, n_jobs=None, precompute_distances='auto',
       random_state=None, tol=0.0001, verbose=0)

In [7]:
normalized['Cluster']= KMean_clust.labels_
normalized['MSISDN']= durationPerUser.keys()
userEngagementDF['MSISDN']= durationPerUser.keys()
normalized.sample(10)

metricDF=userEngagementDF[['Session Frequency','Session Duration','Total Data']]
metricDF['Cluster']=KMean_clust.labels_

## Cluster 0 has the lowest mean in all of the metrics. So cluster 0 is the cluster with the lowest engagement.

In [8]:
clusteredMean = metricDF.groupby('Cluster').mean()
clusteredMean

Session Frequency  Session Duration    Total Data
Cluster                                                   
0                 1.042273     106993.096203  4.955116e+08
1                 4.249938     569765.059345  2.281370e+09
2                 2.176443     213620.305829  1.125692e+09

### The following cell determines the centroid of each cluster and use it the centroid of the less engaged cluster to calculate the score for each user.

In [9]:
centroids = KMean_clust.cluster_centers_
centroids = min_max_scaler.inverse_transform(centroids)
print(centroids)
userEngagementDF['Score'] = np.linalg.norm( userEngagementDF[['Session Frequency', 'Session Duration','Total Data']].sub(np.array(centroids[0])), axis=1)
userEngagementDF

[[1.04212005e+00 1.06976916e+05 4.95491865e+08]
 [4.24735937e+00 5.69228913e+05 2.27996678e+09]
 [2.17586430e+00 2.13553199e+05 1.12511705e+09]]


MSISDN  Session Frequency  Session Duration    Total Data  \
0       3.360100e+10                  1          116720.0  8.786906e+08   
1       3.360100e+10                  1          181230.0  1.568596e+08   
2       3.360100e+10                  1          134969.0  5.959665e+08   
3       3.360101e+10                  1           49878.0  4.223207e+08   
4       3.360101e+10                  2           37104.0  1.457411e+09   
...              ...                ...               ...           ...   
106851  3.379000e+10                  1            8810.0  7.146416e+08   
106852  3.379000e+10                  1          140988.0  4.803073e+08   
106853  3.197021e+12                  1          877385.0  2.321240e+08   
106854  3.370000e+14                  1          253030.0  5.962878e+08   
106855  8.823971e+14                  1          869844.0  1.391536e+08   

               Score  
0       3.831987e+08  
1       3.386322e+08  
2       1.004746e+08  
3       7.317119e+07  
4       9.619191e+08  
...              ...  
106851  2.191498e+08  
106852  1.518457e+07  
106853  2.633690e+08  
106854  1.007961e+08  
106855  3.563390e+08  

[106856 rows x 5 columns]

## The following cells cluster users based on the experience metrics.

In [10]:
dataFrame=dataFrame.rename(columns = {'Total DL (Bytes)' : 'totalDL','Total UL (Bytes)' : 'totalUL','Dur. (ms)' : 
                                      'dur','msisdn':'MSISDN','Last Location Name':'location',
                                      'Handset Manufacturer':'manufacturer','Handset Type':'handset',
                                      'Avg RTT DL (ms)':'AVG RTT DL',
                                      'Avg RTT UL (ms)':'AVG RTT UL',
                                      'Avg Bearer TP UL (kbps)':'AVG TP UL',
                                      'Avg Bearer TP DL (kbps)':'AVG TP DL',
                                      'TCP UL Retrans. Vol (Bytes)':'TCP UL Retrans',
                                      'TCP DL Retrans. Vol (Bytes)':'TCP DL Retrans'
                                      
                                     
                                     })
userExperienceDF=dataFrame[['AVG RTT DL','AVG RTT UL','TCP UL Retrans','TCP DL Retrans','AVG TP UL','AVG TP DL']]
sumNull = userExperienceDF.isnull().sum()

for column in userExperienceDF.columns:
    if(column=='handset'):
        userExperienceDF[column] = userExperienceDF[column].fillna( userExperienceDF[column].mode().values[0] )
        userExperienceDF[column] = userExperienceDF[column].replace(['undefined'],userExperienceDF[column].mode().values[0])
    else:
        userExperienceDF[column] = userExperienceDF[column].fillna( userExperienceDF[column].mean() )
columns=userExperienceDF.columns
i=1
for column in columns:
    if(column!='handset'):
        Q1=userExperienceDF[column].quantile(0.25)
        Q3=userExperienceDF[column].quantile(0.75)
        IQR=Q3-Q1
        Lower_Whisker = Q1-1.5*IQR
        Upper_Whisker = Q3+1.5*IQR
        #print(Lower_Whisker, Upper_Whisker)
        userExperienceDF.loc[userExperienceDF[column] > Upper_Whisker, column] = userExperienceDF[column].mean()
userExperienceDF['AVG TCP'] = userExperienceDF['TCP UL Retrans']+userExperienceDF['TCP DL Retrans']
userExperienceDF['AVG RTT'] = userExperienceDF['AVG RTT UL']+userExperienceDF['AVG RTT DL']
userExperienceDF['AVG TP'] = userExperienceDF['AVG TP UL']+userExperienceDF['AVG TP DL']

userExperienceDF['MSISDN'] = dataFrame['MSISDN']
userExperienceTotalDF=userExperienceDF[['MSISDN','AVG TCP','AVG RTT','AVG TP']]
experiencePerUserDF = userExperienceTotalDF.groupby('MSISDN').sum()

experiencePerUserDF

C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:21: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
C:\ProgramData\Anaconda3\lib\site-packages\pandas\core\indexing.py:670: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_with_indexer(indexer, value)
C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:32: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-

AVG TCP     AVG RTT        AVG TP
MSISDN                                              
3.360100e+10  2.156957e+07   46.000000     76.000000
3.360100e+10  2.156957e+07   31.000000     99.000000
3.360100e+10  2.156957e+07  127.458589     97.000000
3.360101e+10  7.607247e+05   84.000000    248.000000
3.360101e+10  3.094040e+07  119.000000  42205.428647
...                    ...         ...           ...
3.379000e+10  2.180450e+05   52.000000  10365.000000
3.379000e+10  2.156957e+07   40.000000    116.000000
3.197021e+12  2.156957e+07  127.458589      1.000000
3.370000e+14  2.156957e+07  127.458589     33.000000
8.823971e+14  2.156957e+07  127.458589      2.000000

[106856 rows x 3 columns]

In [11]:
x = experiencePerUserDF[['AVG TCP','AVG RTT','AVG TP']].values.astype(float)
min_max_scaler = preprocessing.MinMaxScaler()
x_scaled = min_max_scaler.fit_transform(x)
normalized = pd.DataFrame(x_scaled,columns=['AVG TCP','AVG RTT','AVG TP'])
KMean_clust= KMeans(n_clusters=3, init='k-means++',max_iter=1000)
KMean_clust.fit(normalized)
metricDF=experiencePerUserDF[['AVG TCP','AVG RTT','AVG TP']]
metricDF['Cluster']=KMean_clust.labels_
metricDF

AVG TCP     AVG RTT        AVG TP  Cluster
MSISDN                                                       
3.360100e+10  2.156957e+07   46.000000     76.000000        1
3.360100e+10  2.156957e+07   31.000000     99.000000        1
3.360100e+10  2.156957e+07  127.458589     97.000000        1
3.360101e+10  7.607247e+05   84.000000    248.000000        2
3.360101e+10  3.094040e+07  119.000000  42205.428647        2
...                    ...         ...           ...      ...
3.379000e+10  2.180450e+05   52.000000  10365.000000        2
3.379000e+10  2.156957e+07   40.000000    116.000000        1
3.197021e+12  2.156957e+07  127.458589      1.000000        1
3.370000e+14  2.156957e+07  127.458589     33.000000        1
8.823971e+14  2.156957e+07  127.458589      2.000000        1

[106856 rows x 4 columns]

### The following cell determines the mean of the experience metrics for each cluster.

In [12]:
clusteredMean = metricDF.groupby('Cluster').mean()
clusteredMean

AVG TCP     AVG RTT        AVG TP
Cluster                                        
0        3.792151e+07  375.682825  84341.961000
1        2.643764e+07   95.464594   2483.454060
2        5.369481e+06   99.597559  21390.423562

### The following cell calculates satisfaction for each user as the average of engagement and experience scores.

In [13]:
centroids = KMean_clust.cluster_centers_
centroids = min_max_scaler.inverse_transform(centroids)

satisfactionDF=experiencePerUserDF
satisfactionDF['Exp Score'] = np.linalg.norm( experiencePerUserDF[['AVG TCP','AVG RTT','AVG TP']].sub(np.array(centroids[0])), axis=1)

# retreive engagement scores
satisfactionDF['Eng Score']=userEngagementDF['Score'].values
col = satisfactionDF.loc[: , "Eng Score":"Exp Score"]
satisfactionDF['Satisfaction'] = experiencePerUserDF[["Eng Score","Exp Score"]].mean(axis=1)
satisfactionDF=satisfactionDF[["Eng Score","Exp Score",'Satisfaction']]
#experiencePerUserDF['Satisfaction']=(experiencePerUserDF['Eng Score'] + experiencePerUserDF['Exp Score'])/2

satisfactionDF.nlargest(10,'Satisfaction')


Eng Score     Exp Score  Satisfaction
MSISDN                                                
3.361489e+10  8.350740e+09  9.651802e+07  4.223629e+09
3.376054e+10  8.019287e+09  2.123069e+08  4.115797e+09
3.362578e+10  8.004150e+09  2.242831e+08  4.114217e+09
3.362632e+10  7.475680e+09  1.989502e+08  3.837315e+09
3.367588e+10  7.395620e+09  1.294534e+08  3.762537e+09
3.365973e+10  7.210372e+09  5.174769e+07  3.631060e+09
3.366646e+10  6.813011e+09  9.309790e+07  3.453054e+09
3.376041e+10  6.636881e+09  7.730305e+07  3.357092e+09
3.366471e+10  6.376527e+09  7.611050e+07  3.226319e+09
3.369879e+10  6.045409e+09  1.058907e+08  3.075650e+09

In [14]:
import numpy as np
from sklearn.linear_model import LinearRegression

x = satisfactionDF[['Eng Score','Exp Score']]
y = satisfactionDF['Satisfaction']
x, y = np.array(x), np.array(y)
model = LinearRegression().fit(x, y)
r_sq = model.score(x, y)
print('coefficient determination:', r_sq)
print('intercept:', model.intercept_)
print('slope:', model.coef_)
y_pred = model.predict(x)
print('predicted response:', y_pred, sep='\n')

coefficient determination: 1.0
intercept: -3.5762786865234375e-07
slope: [0.5 0.5]
predicted response:
[1.99764574e+08 1.77481334e+08 5.84025300e+07 ... 1.39849730e+08
 5.85632516e+07 1.86334737e+08]


### The following cell runs k-means based engagement and experience score to group users into 2 clusters.

In [15]:
x = satisfactionDF[['Eng Score','Exp Score']].values.astype(float)
min_max_scaler = preprocessing.MinMaxScaler()
x_scaled = min_max_scaler.fit_transform(x)
normalized = pd.DataFrame(x_scaled,columns=['Eng Score','Exp Score'])
KMean_clust= KMeans(n_clusters=2, init='k-means++',max_iter=1000)
KMean_clust.fit(normalized)
satisfactionDF['Cluster']=KMean_clust.labels_
satisfactionDF

C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  import sys


Eng Score     Exp Score  Satisfaction  Cluster
MSISDN                                                         
3.360100e+10  3.831987e+08  1.633044e+07  1.997646e+08        1
3.360100e+10  3.386322e+08  1.633044e+07  1.774813e+08        1
3.360100e+10  1.004746e+08  1.633044e+07  5.840253e+07        1
3.360101e+10  7.317119e+07  3.713916e+07  5.515518e+07        0
3.360101e+10  9.619191e+08  6.959516e+06  4.844393e+08        1
...                    ...           ...           ...      ...
3.379000e+10  2.191498e+08  3.768182e+07  1.284158e+08        0
3.379000e+10  1.518457e+07  1.633044e+07  1.575750e+07        1
3.197021e+12  2.633690e+08  1.633044e+07  1.398497e+08        1
3.370000e+14  1.007961e+08  1.633044e+07  5.856325e+07        1
8.823971e+14  3.563390e+08  1.633044e+07  1.863347e+08        1

[106856 rows x 4 columns]

### The following cell aggregates the average engagement and experience score for each cluster.

In [16]:
satisfactionDF.groupby('Cluster')[['Eng Score','Exp Score']].mean()

Eng Score     Exp Score
Cluster                            
0        3.725139e+08  3.619825e+07
1        3.435433e+08  1.449144e+07

## The following cell exports the dataframe containing engagement score, experience score and satisfaction to SQL. 

In [17]:
import sqlite3
con = sqlite3.connect ('telecom.db')
#print('The python version is...',sqlite3.version)

cursor = con.cursor ()
try:
    cur.execute ('create table user_satisfaction_level (user_id, eng_score number, exp_score number, Satisfaction)')
except :
    print('Table exists.... continuing')

satisfactionDF=satisfactionDF.rename(columns={"Eng Score": "eng_score", "Exp Score": "exp_score"})
satisfactionDF['user_id']=satisfactionDF.index
satisfactionDF[['user_id','eng_score','exp_score','Satisfaction']].to_sql('user_satisfaction_level', con, if_exists='replace', index=False)

satisfactionDF

Table exists.... continuing


eng_score     exp_score  Satisfaction  Cluster       user_id
MSISDN                                                                       
3.360100e+10  3.831987e+08  1.633044e+07  1.997646e+08        1  3.360100e+10
3.360100e+10  3.386322e+08  1.633044e+07  1.774813e+08        1  3.360100e+10
3.360100e+10  1.004746e+08  1.633044e+07  5.840253e+07        1  3.360100e+10
3.360101e+10  7.317119e+07  3.713916e+07  5.515518e+07        0  3.360101e+10
3.360101e+10  9.619191e+08  6.959516e+06  4.844393e+08        1  3.360101e+10
...                    ...           ...           ...      ...           ...
3.379000e+10  2.191498e+08  3.768182e+07  1.284158e+08        0  3.379000e+10
3.379000e+10  1.518457e+07  1.633044e+07  1.575750e+07        1  3.379000e+10
3.197021e+12  2.633690e+08  1.633044e+07  1.398497e+08        1  3.197021e+12
3.370000e+14  1.007961e+08  1.633044e+07  5.856325e+07        1  3.370000e+14
8.823971e+14  3.563390e+08  1.633044e+07  1.863347e+08        1  8.823971e+14

[106856 rows x 5 columns]

In [18]:
cursor.execute("SELECT * FROM user_satisfaction_level")

rows = cursor.fetchall()
rows=rows[:-10]
for row in rows:
        print(row)

    
con.close ()

(33601001722.0, 383198708.9718572, 16330438.347616618, 199764573.6597369)
(33601001754.0, 338632230.292873, 16330438.229328943, 177481334.26110098)
(33601002511.0, 100474621.74727215, 16330438.237890728, 58402529.99258144)
(33601007832.0, 73171189.43049125, 37139164.552196436, 55155176.99134384)
(33601008617.0, 961919081.3857472, 6959516.4554608045, 484439298.920604)
(33601010682.0, 119725446.0994731, 15567989.9177708, 67646718.00862195)
(33601011634.0, 159231202.2837572, 16220042.997249255, 87725622.64050323)
(33601011959.0, 162831509.45227736, 37139950.3031948, 99985729.87773608)
(33601014694.0, 494640476.5924848, 5240026.756386292, 249940251.67443553)
(33601020306.0, 236971896.52231577, 17088793.029987566, 127030344.77615167)
(33601021045.0, 380515855.4416826, 16330438.342811361, 198423146.89224696)
(33601021217.0, 134600586.30928397, 23305239.869525317, 78952913.08940464)
(33601022743.0, 13072786.68711159, 16330438.383578122, 14701612.535344856)
(33601024291.0, 136580032.2077181, 1

(33607554021.0, 259074401.4194099, 16330438.07808981, 137702419.74874985)
(33607555569.0, 16189977.479854649, 16330438.258514488, 16260207.869184569)
(33607557976.0, 24406752.986217067, 16330438.239682766, 20368595.612949915)
(33607560523.0, 393551141.3531897, 16330438.660873627, 204940790.00703168)
(33607560951.0, 109479508.90994246, 36167585.70001286, 72823547.30497766)
(33607561832.0, 342453026.545718, 4481775.489569026, 173467401.0176435)
(33607564187.0, 41689336.38351338, 36866428.16329687, 39277882.27340513)
(33607567836.0, 46367480.98803567, 37740010.6681259, 42053745.82808079)
(33607568190.0, 172420107.5756118, 16326019.159760272, 94373063.36768603)
(33607572841.0, 265270652.9500757, 37133164.247278504, 151201908.5986771)
(33607573370.0, 758480257.8606151, 5240027.695149601, 381860142.7778824)
(33607574957.0, 282773256.6240927, 37895622.43269943, 160334439.52839607)
(33607575685.0, 1609263553.0413074, 26809056.44557286, 818036304.7434402)
(33607577919.0, 191001351.38366076, 163

(33610330045.0, 298146993.144392, 34621828.64440729, 166384410.89439964)
(33610330647.0, 429330159.36808777, 15888394.169212814, 222609276.7686503)
(33610330924.0, 357490506.41085654, 37757342.1525811, 197623924.28171882)
(33610331126.0, 217570644.05678326, 16330438.48146491, 116950541.26912409)
(33610332578.0, 89314814.56505962, 16330438.062628329, 52822626.31384397)
(33610333840.0, 39615834.408384405, 16330438.172662312, 27973136.290523358)
(33610334121.0, 538492471.8762352, 13274209.258509414, 275883340.5673723)
(33610335722.0, 150354117.4990681, 17087291.316566054, 83720704.40781708)
(33610337274.0, 255272091.5419857, 16330438.373649403, 135801264.95781755)
(33610340785.0, 317030933.75179607, 16330438.212112406, 166680685.98195425)
(33610341039.0, 398249911.48800755, 16330438.316379372, 207290174.90219346)
(33610341642.0, 25048576.12857465, 17081240.94552243, 21064908.53704854)
(33610342543.0, 354432904.75796115, 17088793.168149203, 185760848.9630552)
(33610343263.0, 57362157.74620

(33613216620.0, 197162067.16837144, 5240027.166740618, 101201047.16755603)
(33613217889.0, 305284998.34095514, 16330438.270368597, 160807718.30566186)
(33613218434.0, 414066669.45539373, 16330437.940518683, 215198553.6979562)
(33613218854.0, 182209572.31071308, 16330438.258514488, 99270005.28461379)
(33613220030.0, 295243543.73537886, 5240025.914089799, 150241784.82473433)
(33613220753.0, 32712530.183916055, 16330438.06454876, 24521484.124232408)
(33613221387.0, 109494748.32452063, 16330438.25934048, 62912593.29193056)
(33613222299.0, 115160472.64009905, 17088887.391838994, 66124680.01596902)
(33613224592.0, 326748149.7037837, 16330438.229371253, 171539293.96657747)
(33613224899.0, 418865485.4285679, 5240026.43541556, 212052755.93199173)
(33613225845.0, 136491957.63276538, 16330438.157412741, 76411197.89508906)
(33613226352.0, 92244024.56306349, 16330437.101350425, 54287230.83220696)
(33613226383.0, 27838869.200909685, 16330438.268826736, 22084653.73486821)
(33613226958.0, 484097697.12

(33615388950.0, 145119633.09598815, 16330438.232734941, 80725035.66436155)
(33615390800.0, 25267119.067055684, 16330372.82950334, 20798745.94827951)
(33615391939.0, 209144811.16608453, 37723636.83788603, 123434224.00198528)
(33615394316.0, 266702788.75401205, 5240026.828578673, 135971407.79129535)
(33615396935.0, 25368560.506983478, 17088793.18230914, 21228676.84464631)
(33615397207.0, 240657755.54241392, 16330438.42482062, 128494096.98361728)
(33615399136.0, 323954732.91061395, 16330438.198167557, 170142585.55439076)
(33615399788.0, 901474480.0681094, 5240027.229446032, 453357253.6487777)
(33615402099.0, 284352939.87473875, 16330438.249385614, 150341689.06206217)
(33615402554.0, 758985387.2781782, 14667764.65613841, 386826575.9671583)
(33615404200.0, 368737785.42218435, 36470279.19885161, 202604032.31051797)
(33615404612.0, 193996333.78389925, 16330438.110243013, 105163385.94707114)
(33615406365.0, 950614131.307877, 5240026.274958814, 477927078.7914179)
(33615407060.0, 25599108.526927

...

(33763509485.0, 288554853.45682096, 5240027.595352265, 146897440.52608663)
(33763510483.0, 1297119011.7687123, 6001437.471804906, 651560224.6202586)
(33763510616.0, 573507935.9937495, 10004027.133294689, 291755981.5635221)
(33763510633.0, 704459954.0156125, 5240026.756386292, 354849990.3859994)
(33763511425.0, 197569795.22438237, 16330423.470718814, 106950109.34755059)
(33763513047.0, 356030138.95801616, 16330438.18744172, 186180288.57272893)
(33763513235.0, 203193364.88998425, 37545548.933560774, 120369456.91177252)
(33763513706.0, 194775189.0266734, 16330438.206956925, 105552813.61681516)
(33763514634.0, 131191302.91111813, 16330438.223985923, 73760870.56755203)
(33763514766.0, 218593049.76350725, 16330438.286302818, 117461744.02490503)
(33763515101.0, 366200346.4281007, 16330438.660873627, 191265392.54448718)
(33763515365.0, 550464621.9139161, 26809050.993610214, 288636836.4537632)
(33763518087.0, 193281624.0761577, 16330438.660873627, 104806031.36851566)
(33763518195.0, 395532340.9

(33768636005.0, 173849209.4811965, 16330438.294608425, 95089823.88790245)
(33768636718.0, 25379909.748633068, 16330438.31187021, 20855174.030251637)
(33768637330.0, 483856092.02481574, 5667392.909583096, 244761742.46719941)
(33768638041.0, 53242192.149223976, 37707932.845066264, 45475062.49714512)
(33768639063.0, 190054040.15277478, 16330438.397750491, 103192239.27526264)
(33768648555.0, 309263128.2585646, 16330438.181809772, 162796783.2201872)
(33768649286.0, 57625315.154003434, 16330438.383480158, 36977876.768741794)
(33768650633.0, 283093840.1477607, 17088793.1867187, 150091316.6672397)
(33768654315.0, 1374073678.344329, 26831625.982082967, 700452652.1632061)
(33768655160.0, 72892628.16642846, 16330438.103860172, 44611533.135144316)
(33768655637.0, 126251864.75140883, 16330438.415015953, 71291151.58321239)
(33768657898.0, 1009084071.3711507, 5240026.346252469, 507162048.8587016)
(33768662996.0, 194892606.9355209, 16330438.337549038, 105611522.63653496)
(33768667482.0, 130109146.5781

(33775264209.0, 414797497.74860567, 37856602.86426274, 226327050.3064342)
(33775268305.0, 269030295.61111104, 6582584.656985104, 137806440.13404807)
(33776031825.0, 139024453.7517493, 16330438.660873627, 77677446.20631146)
(33776092862.0, 274204487.6981907, 5240026.475860632, 139722257.08702567)
(33776118028.0, 351004470.1614576, 16330438.660873627, 183667454.41116562)
(33776140203.0, 110740091.73423816, 16330438.27459477, 63535265.004416466)
(33776144339.0, 1344513320.1236992, 16254111.165538536, 680383715.6446189)
(33776147191.0, 175768819.29801792, 14760853.4010688, 95264836.34954336)
(33776339403.0, 301835265.16374266, 16330438.660873627, 159082851.91230816)
(33776393154.0, 156923204.3253984, 16330438.187577154, 86626821.25648777)
(33776578152.0, 217506956.00866443, 16330420.499699008, 116918688.25418171)
(33776623583.0, 215882741.88132396, 16330438.660873627, 116106590.2710988)
(33776690451.0, 116270372.08587228, 37894501.44102038, 77082436.76344633)
(33776696063.0, 279276482.8883

(33782974852.0, 759337334.6603914, 5240027.742874752, 382288681.2016331)
(33782977946.0, 77602386.38277869, 16330438.229182793, 46966412.30598074)
(33782980777.0, 582410443.0066409, 477310.9473481755, 291443876.9769945)
(33782981280.0, 855006036.7645452, 16321924.372740706, 435663980.568643)
(33782982242.0, 37976846.14731571, 36078870.46979012, 37027858.30855292)
(33782983382.0, 443475751.1763092, 16330438.270246813, 229903094.72327802)
(33782984587.0, 321577073.84212226, 16027284.900697159, 168802179.3714097)
(33782984971.0, 176643874.3833269, 37099407.83935471, 106871641.11134079)
(33782990926.0, 12156642.181529233, 16330438.306713566, 14243540.244121399)
(33782991542.0, 157724230.84442028, 16330438.212112406, 87027334.52826634)
(33782991971.0, 286825444.24060005, 37897870.06185423, 162361657.15122715)
(33782992285.0, 147762206.47493732, 16330438.177506022, 82046322.32622167)
(33782993222.0, 955319996.8905206, 5240027.693805524, 480280012.2921631)
(33782993676.0, 620343678.5654942, 1

(33788072702.0, 56378114.60344719, 37590516.44871342, 46984315.52608031)
(33788076642.0, 153204466.26215434, 16330438.279139228, 84767452.27064678)
(33788078143.0, 125473020.13360259, 16330438.621049305, 70901729.37732595)
(33788100055.0, 373144331.2795967, 16330438.414407043, 194737384.84700185)
(33788102860.0, 24946863.620004717, 16330438.341881867, 20638650.980943292)
(33788110325.0, 36975122.82020541, 37747711.127924, 37361416.97406471)
(33788116172.0, 323901106.05459875, 16330438.660873627, 170115772.3577362)
(33788128032.0, 45954686.422641024, 16330438.454489069, 31142562.438565046)
(33788144687.0, 3564271.9640253196, 16330438.222423552, 9947355.093224436)
(33788146537.0, 93183366.21843708, 16330438.373566257, 54756902.296001665)
(33788152076.0, 382127269.7744868, 16330438.224452663, 199228853.99946973)
(33788153792.0, 888032818.5117763, 5240027.735818368, 446636423.12379736)
(33788154609.0, 37390359.77492502, 37123885.09510623, 37257122.435015626)
(33788159194.0, 210527188.61716